In [2]:
# Add packages to notebook
import pandas as pd  # provides interface for interacting with tabular data
import geopandas as gpd  # combines the capabilities of pandas and shapely for geospatial operations
import matplotlib.pyplot as plt
from bokeh.plotting import figure, show
from bokeh.models import GeoJSONDataSource, HoverTool, LinearColorMapper, ColorBar, WheelZoomTool
from bokeh.tile_providers import get_provider, Vendors
from bokeh.io import output_notebook
import geopandas as gpd
from bokeh.palettes import Blues



# Import PUDs file as a geodataframe and initialize Coordinate Reference System (CRS)
cev = gpd.read_file('calenviroscreen/CES4 Final Shapefile.shp', crs = {'init' :'epsg:4326'})

In [3]:
#cleaning and filtering LA country data
cev['coords'] = cev['geometry'].apply(lambda x: x.representative_point().coords[:])
cev['coords'] = [coords[0] for coords in cev['coords']]
cevLA = cev[(cev['County']=="Los Angeles") & (cev['ApproxLoc']!="Unincorporated Los Angeles County area") &(cev['CIscore']>0)]

In [4]:
# Define the color mapper
color_mapper = LinearColorMapper(palette=Blues[256], low=cevLA['CIscore'].max(), high=cevLA['CIscore'].min())

def make_plot(geo_source):
    """make Bokeh plot of calEnviroScreen scores"""
    TOOLTIPS = [
        ('City', '@ApproxLoc'),
        ('CIscore', '@CIscore')
    ]
    hover = HoverTool(tooltips=TOOLTIPS)

    p = figure(
        title="Cal EnviroScreen",
        x_axis_type="mercator", y_axis_type="mercator",
        tools=[hover, 'pan', WheelZoomTool(), 'reset'],
        background_fill_color='gray',
        plot_width=800, plot_height=1000
    )
    p.add_tile(get_provider(Vendors.CARTODBPOSITRON))
    p.patches('xs', 'ys', source=geo_source,
              fill_color={'field': 'CIscore', 'transform': color_mapper},
              fill_alpha=1, line_color='white', line_width=0.25)
    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='horizontal')
    p.add_layout(color_bar, 'below')
    return p

In [5]:
#plot for LA County
cevLA_json = cevLA.to_json()
geo_sourceLA = GeoJSONDataSource(geojson=cevLA_json)
output_notebook(hide_banner=True)
plot = make_plot(geo_sourceLA)
show(plot)


In [7]:
# run this cell if you want to see CA map
"""
cev_json = cev.to_json()
geo_sourceCA = GeoJSONDataSource(geojson=cev_json)
output_notebook(hide_banner=True)
plot = make_plot(geo_sourceCA)
show(plot)
"""

'\ncev_json = cev.to_json()\ngeo_sourceCA = GeoJSONDataSource(geojson=cev_json)\noutput_notebook(hide_banner=True)\nplot = make_plot(geo_sourceCA)\nshow(plot)\n'